# PLS decomposition of the codon space

In [68]:
import numpy as np
import pandas as pd

# sklearn import
from sklearn.preprocessing import PolynomialFeatures, StandardScaler
from sklearn.pipeline import Pipeline
from sklearn.feature_selection import VarianceThreshold
from sklearn.cross_decomposition import PLSRegression
import joblib

# my module imports
from optimalcodon.projects.rnastability.dataprocessing import get_data, general_preprocesing_pipeline
from optimalcodon.projects.rnastability import modelevaluation

import matplotlib.pyplot as plt
%config InlineBackend.figure_format = 'svg'

In [6]:
(train_x, train_y), (test_x, test_y) = get_data("../19-04-30-PredictiveModelDecayAllSpecies/19-04-30-EDA/results_data/")

## What is the optimal number of components?

In [14]:
preprocessing = Pipeline([
    ('general', general_preprocesing_pipeline(train_x)),
    ('polyfeaturs', PolynomialFeatures(degree=2)),
    ('zerovar', VarianceThreshold(threshold=0.0)),
    ('scaling', StandardScaler())
])

preprocessing.fit(train_x)
train_x_transformed = preprocessing.transform(train_x)

In [15]:
pls_reg = Pipeline([
    ('pls', PLSRegression())
])

pls_grid = dict(
    pls__n_components = np.arange(6, 15, 1)
)

pls_search = modelevaluation.gridsearch(pls_reg, pls_grid, train_x_transformed, train_y)

Fitting 3 folds for each of 9 candidates, totalling 27 fits


[Parallel(n_jobs=32)]: Using backend LokyBackend with 32 concurrent workers.
[Parallel(n_jobs=32)]: Done   3 out of  27 | elapsed:  1.4min remaining: 11.5min
[Parallel(n_jobs=32)]: Done   6 out of  27 | elapsed:  1.5min remaining:  5.3min
[Parallel(n_jobs=32)]: Done   9 out of  27 | elapsed:  1.6min remaining:  3.3min
[Parallel(n_jobs=32)]: Done  12 out of  27 | elapsed:  1.7min remaining:  2.1min
[Parallel(n_jobs=32)]: Done  15 out of  27 | elapsed:  1.7min remaining:  1.4min
[Parallel(n_jobs=32)]: Done  18 out of  27 | elapsed:  1.8min remaining:   54.6s
[Parallel(n_jobs=32)]: Done  21 out of  27 | elapsed:  1.9min remaining:   32.7s
[Parallel(n_jobs=32)]: Done  24 out of  27 | elapsed:  2.0min remaining:   15.3s
[Parallel(n_jobs=32)]: Done  27 out of  27 | elapsed:  2.2min remaining:    0.0s
[Parallel(n_jobs=32)]: Done  27 out of  27 | elapsed:  2.2min finished


Best Score R2 =  0.19312240722861246
Best Parameters:  {'pls__n_components': 9}


In [19]:
## train pipeline with the optimal number of components
pls_decomposition = Pipeline([
    ('general', general_preprocesing_pipeline(train_x)),
    ('polyfeaturs', PolynomialFeatures(degree=2)),
    ('zerovar', VarianceThreshold(threshold=0.0)),
    ('scaling', StandardScaler()),
    ('pls', PLSRegression(n_components=pls_search.best_params_['pls__n_components']))
])

In [32]:
X = pd.concat([test_x, train_x])
y = pd.concat([test_y, train_y])

# train pipeline in the whole data

In [34]:
X.head()

specie cell_type  datatype  \
gene_id                                      
ENSG00000004961  human      k562  slam-seq   
ENSG00000006695  human      k562  slam-seq   
ENSG00000006715  human      k562  slam-seq   
ENSG00000007923  human      k562  slam-seq   
ENSG00000008838  human      k562  slam-seq   

                                                            coding  utrlenlog  \
gene_id                                                                         
ENSG00000004961  ATGGGTTTGTCTCCATCTGCTCCTGCTGTTGCAGTTCAGGCCTCAA...   7.152269   
ENSG00000006695  ATGGCCGCATCTCCGCACACTCTCTCCTCACGCCTCCTGACAGGTT...   7.289611   
ENSG00000006715  ATGGCGGAAGCAGAGGAGCAGGAAACTGGGTCCCTTGAAGAATCTA...   8.093462   
ENSG00000007923  ATGGCGACGGCCTTGAGCGAGGAGGAGCTGGACAATGAAGACTATT...   7.317212   
ENSG00000008838  ATGTCCTTTTCTTTAGCTCCATTTCTTTCACCTCAAAGCTGGCCGC...   7.989560   

                 cdslenlog  
gene_id                     
ENSG00000004961   6.694562  
ENSG00000006695   7.195187  
ENSG00000006715   7.850104  
ENSG00000007923   7.427144  
ENSG00000008838   8.021585

In [36]:
pls_decomposition.fit(X, y)

Pipeline(memory=None,
     steps=[('general', Pipeline(memory=None,
     steps=[('specific feature pipe', ColumnTransformer(n_jobs=None, remainder='drop', sparse_threshold=0.3,
         transformer_weights=None,
         transformers=[('codons', Pipeline(memory=None,
     steps=[('codon composition', CodonCompositionTransform..._std=True)), ('pls', PLSRegression(copy=True, max_iter=500, n_components=9, scale=True, tol=1e-06))])

In [38]:
y_pred = pls_decomposition.predict(X)

In [44]:
plt.scatter(y_pred, y, s=1/5)
plt.xlabel('predicted')
plt.ylabel('observed')

Text(0, 0.5, 'observed')

## Get PLS decomposition

In [58]:
components = pls_decomposition.transform(X)
components = pd.DataFrame(components, columns=['PLS_' + str(x) for x in range(1, 10)])
components.index = X.index

In [65]:
## merge the data

components = pd.concat([X, components], axis=1).drop(['coding', 'utrlenlog', 'cdslenlog'], axis=1)
components['decay_scaled'] = y

In [67]:
components.to_csv("results_data/pls_decomposition_all.csv")

In [69]:
## SAVE DECOMPOSITION PIPELINE
joblib.dump(pls_decomposition, 'results_data/pls_decomposition.joblib')

['results_data/pls_decomposition.joblib']